In [36]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)
import random
import matplotlib.pyplot as plt

seed_value=3
random.seed(seed_value)

distribution="double normal" # 二谷正規分布

#要素
j_mean1,j_std_dev1= 5,1  # ジョブ数第一谷平均値、標準偏差
j_mean2,j_std_dev2= 8,1  # ジョブ数第二谷平均値、標準偏差
j_size = 1000  # ジョブ数样本サイズ
j_weight1, j_weight2 = 0.5, 0.5

p_mean1,p_std_dev1= 5,1  # 各ジョブのプロセス数第一谷平均値、標準偏差
p_mean2,p_std_dev2= 8,1  # 各ジョブのプロセス数第二谷平均値、標準偏差
p_size = 1000  # 各ジョブのプロセス数样本サイズ
p_weight1, p_weight2 = 0.5, 0.5

m_low=1 #最小機械番号
m_high=5 #最大機械番号

t_mean1,t_std_dev1= 10,1  # 操作時間第一谷平均値、標準偏差
t_mean2,t_std_dev2= 15,1  # 操作時間第二谷平均値、標準偏差
t_size = 1000  # 操作時間样本サイズ
t_weight1, t_weight2 = 0.5, 0.5

gene=10000
for g in np.arange(0,gene):
    
    #ジョブ数固定
    j_data1 = np.random.normal(j_mean1, j_std_dev1, int(j_size * j_weight1))
    j_data2 = np.random.normal(j_mean2, j_std_dev2, int(j_size * j_weight2))
    j_data = np.concatenate([j_data1, j_data2]).astype(int)
    j_number=j_data[np.random.randint(0,1000)] # ジョブ数
    while j_number <= 1 :
        j_number=j_data[np.random.randint(0,1000)]
    #print("ジョブ数は：",j_number)
    #plt.hist(j_data, bins=30, density=True, alpha=0.6, color='blue', edgecolor='black')

    #各ジョブのプロセス数固定
    p_data1 = np.random.normal(p_mean1, p_std_dev1, int(p_size * p_weight1))
    p_data2 = np.random.normal(p_mean2, p_std_dev2, int(p_size * p_weight2))
    p_data = np.concatenate([p_data1, p_data2]).astype(int)
    p_number=p_data[:j_number]#各ジョブのプロセス数
    #print("各ジョブのプロセス数は：",p_number)
    p_number_max=max(p_number)
    #print("最大プロセス数：",p_number_max)
    #plt.hist(p_data, bins=30, density=True, alpha=0.6, color='blue', edgecolor='black')

    #各プロセス機械割り当て
    MS_J=np.zeros((int(j_number),int(p_number_max)))
    for i in np.arange(0,j_number):
        k=int(p_number[i])
        for j in np.arange(0,k):
            MS_J[i,j]=np.random.randint(m_low,m_high,1)
            if j > 0:
                while True:
                    MS_J[i,j]=np.random.randint(m_low,m_high,1)
                    if MS_J[i,j]!=MS_J[i,j-1]:
                        break
    #print('ジョブセットの機械番号:\n',MS_J)

    #各プロセス要する操作時間固定
    T_J=np.zeros((int(j_number),int(p_number_max)))
    t_data1 = np.random.normal(t_mean1, t_std_dev1, int(t_size * t_weight1))
    t_data2 = np.random.normal(t_mean2, t_std_dev2, int(t_size * t_weight2))
    t_data = np.concatenate([t_data1, t_data2]).astype(int)
    #plt.hist(t_data, bins=30, density=True, alpha=0.6, color='blue', edgecolor='black')
    for i in np.arange(0,j_number):
        k=int(p_number[i])
        for j in np.arange(0,k):
            T_J[i,j]=t_data[np.random.randint(0,1000)]
    #print('ジョブセットの操作時間:\n',T_J)

    JOBSET_0=np.zeros((int(j_number),int(p_number_max)))
    JOBSET=pd.DataFrame(JOBSET_0, columns=[f"process{i+1}" for i in range(int(p_number_max))], index=[f"job{i+1}" for i in range(int(j_number))])
    JOBSET=JOBSET.astype(str)

    for i in np.arange(0,j_number):
        k=int(p_number[i])
        for j in np.arange(0,k):
            m=MS_J[i,j]
            t=T_J[i,j]
            JOBSET.iloc[i,j]=str(m),str(t)    
    #print('自動生成したジョブセット：\n',JOBSET)
    
    str1="D://pysrc/wang_data/jobset/"+str(distribution)+"/"
    j_element="j1["+str(j_mean1)+","+str(j_std_dev1)+"],j2["+str(j_mean2)+","+str(j_std_dev2)+"]/"
    p_element="p1["+str(p_mean1)+","+str(p_std_dev1)+"],p2["+str(p_mean2)+","+str(p_std_dev2)+"]/"
    m_element="machine["+str(m_high-1)+"]/"
    t_element="t1["+str(t_mean1)+","+str(t_std_dev1)+"],t2["+str(t_mean2)+","+str(t_std_dev2)+"]/"
    file="seed["+str(seed_value)+"]/"
    name="["+str(j_number)+']r['+str(p_number_max)+']c,'+str(g)+'gene'
    str2=".csv"

    filename=str1+j_element+p_element+m_element+t_element+file+name+str2
    
    JOBSET.to_csv(filename,index=True)


C:\Users\G15\AppData\Local\Temp\ipykernel_16380\695042608.py:60: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  MS_J[i,j]=np.random.randint(m_low,m_high,1)
C:\Users\G15\AppData\Local\Temp\ipykernel_16380\695042608.py:63: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  MS_J[i,j]=np.random.randint(m_low,m_high,1)
C:\Users\G15\AppData\Local\Temp\ipykernel_16380\695042608.py:60: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  MS_J[i,j]=np.random.randint(m_low,m_high,1)
C:\U